## Importing all necessary libraries

In [95]:
!pip install requests
!pip install beautifulsoup4
print('Installation completed.')

Installation completed.


In [96]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

from bs4 import BeautifulSoup
import requests # library to handle requests

import lxml.html as lh

print('Libraries imported.')

Libraries imported.


# Scraping Data from Wikipedia:

In [97]:
url = "https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"

#Create a handle, page, to handle the contents of the website
page = requests.get(url)
#Store the contents of the website under doc
doc = lh.fromstring(page.content)
#Parse data that are stored between <tr>..</tr> of HTML
tr_elements = doc.xpath('//tr')

In [98]:
tr_elements = doc.xpath('//tr')
#Create empty list
col=[]
i=0
#For each row, store each first element (header) and an empty list
for t in tr_elements[0]:
    i+=1
    name=t.text_content()
    print(i,name)
    col.append((name,[]))

1 Postal Code

2 Borough

3 Neighbourhood



In [99]:
#Since out first row is the header, data is stored on the second row onwards
for j in range(1, len(tr_elements)):
    #T is our j'th row
    T = tr_elements[j]
    
    #If row is not of size 10, the //tr data is not from our table 
    if len(T) != 3:
        break
    
    #i is the index of our column
    i = 0
    
    #Iterate through each element of the row
    for t in T.iterchildren():
        data=t.text_content() 
        #Check if row is empty
        if i > 0:
        #Convert any numerical value to integers
            try:
                data = int(data)
            except:
                pass
        #Append the data to the empty list of the i'th column
        col[i][1].append(data)
        #Increment i for the next column
        i+=1

In [100]:
Dict = {title:column for (title,column) in col}
df = pd.DataFrame(Dict)
df.head()

Postal Code\n           Borough\n              Neighbourhood\n
0         M1A\n      Not assigned\n               Not assigned\n
1         M2A\n      Not assigned\n               Not assigned\n
2         M3A\n        North York\n                  Parkwoods\n
3         M4A\n        North York\n           Victoria Village\n
4         M5A\n  Downtown Toronto\n  Regent Park, Harbourfront\n

In [101]:
df = df.replace('\n','', regex = True)
df.rename(columns={'Neighbourhood': 'Neighborhood'}, inplace=True)
df

Postal Code\n              Borough\n  \
0             M1A           Not assigned   
1             M2A           Not assigned   
2             M3A             North York   
3             M4A             North York   
4             M5A       Downtown Toronto   
5             M6A             North York   
6             M7A       Downtown Toronto   
7             M8A           Not assigned   
8             M9A              Etobicoke   
9             M1B            Scarborough   
10            M2B           Not assigned   
11            M3B             North York   
12            M4B              East York   
13            M5B       Downtown Toronto   
14            M6B             North York   
15            M7B           Not assigned   
16            M8B           Not assigned   
17            M9B              Etobicoke   
18            M1C            Scarborough   
19            M2C           Not assigned   
20            M3C             North York   
21            M4C              East York   
22            M5C       Downtown Toronto   
23            M6C                   York   
24            M7C           Not assigned   
25            M8C           Not assigned   
26            M9C              Etobicoke   
27            M1E            Scarborough   
28            M2E           Not assigned   
29            M3E           Not assigned   
30            M4E           East Toronto   
31            M5E       Downtown Toronto   
32            M6E                   York   
33            M7E           Not assigned   
34            M8E           Not assigned   
35            M9E           Not assigned   
36            M1G            Scarborough   
37            M2G           Not assigned   
38            M3G           Not assigned   
39            M4G              East York   
40            M5G       Downtown Toronto   
41            M6G       Downtown Toronto   
42            M7G           Not assigned   
43            M8G           Not assigned   
44            M9G           Not assigned   
45            M1H            Scarborough   
46            M2H             North York   
47            M3H             North York   
48            M4H              East York   
49            M5H       Downtown Toronto   
50            M6H           West Toronto   
51            M7H           Not assigned   
52            M8H           Not assigned   
53            M9H           Not assigned   
54            M1J            Scarborough   
55            M2J             North York   
56            M3J             North York   
57            M4J              East York   
58            M5J       Downtown Toronto   
59            M6J           West Toronto   
60            M7J           Not assigned   
61            M8J           Not assigned   
62            M9J           Not assigned   
63            M1K            Scarborough   
64            M2K             North York   
65            M3K             North York   
66            M4K           East Toronto   
67            M5K       Downtown Toronto   
68            M6K           West Toronto   
69            M7K           Not assigned   
70            M8K           Not assigned   
71            M9K           Not assigned   
72            M1L            Scarborough   
73            M2L             North York   
74            M3L             North York   
75            M4L           East Toronto   
76            M5L       Downtown Toronto   
77            M6L             North York   
78            M7L           Not assigned   
79            M8L           Not assigned   
80            M9L             North York   
81            M1M            Scarborough   
82            M2M             North York   
83            M3M             North York   
84            M4M           East Toronto   
85            M5M             North York   
86            M6M                   York   
87            M7M           Not assigned   
88            M8M           Not assigned   
89            M9M             North York   


In [102]:
# drop last row
df = df[:-1]

# remove whitespace in column names
df.columns = df.columns.str.strip()

# remove rows which have "Not assigned" borough
df = df[df['Borough'] != "Not assigned"]
df

Postal Code           Borough  \
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
5           M6A        North York   
6           M7A  Downtown Toronto   
8           M9A         Etobicoke   
9           M1B       Scarborough   
11          M3B        North York   
12          M4B         East York   
13          M5B  Downtown Toronto   
14          M6B        North York   
17          M9B         Etobicoke   
18          M1C       Scarborough   
20          M3C        North York   
21          M4C         East York   
22          M5C  Downtown Toronto   
23          M6C              York   
26          M9C         Etobicoke   
27          M1E       Scarborough   
30          M4E      East Toronto   
31          M5E  Downtown Toronto   
32          M6E              York   
36          M1G       Scarborough   
39          M4G         East York   
40          M5G  Downtown Toronto   
41          M6G  Downtown Toronto   
45          M1H       Scarborough   
46          M2H        North York   
47          M3H        North York   
48          M4H         East York   
49          M5H  Downtown Toronto   
50          M6H      West Toronto   
54          M1J       Scarborough   
55          M2J        North York   
56          M3J        North York   
57          M4J         East York   
58          M5J  Downtown Toronto   
59          M6J      West Toronto   
63          M1K       Scarborough   
64          M2K        North York   
65          M3K        North York   
66          M4K      East Toronto   
67          M5K  Downtown Toronto   
68          M6K      West Toronto   
72          M1L       Scarborough   
73          M2L        North York   
74          M3L        North York   
75          M4L      East Toronto   
76          M5L  Downtown Toronto   
77          M6L        North York   
80          M9L        North York   
81          M1M       Scarborough   
82          M2M        North York   
83          M3M        North York   
84          M4M      East Toronto   
85          M5M        North York   
86          M6M              York   
89          M9M        North York   
90          M1N       Scarborough   
91          M2N        North York   
92          M3N        North York   
93          M4N   Central Toronto   
94          M5N   Central Toronto   
95          M6N              York   
98          M9N              York   
99          M1P       Scarborough   
100         M2P        North York   
102         M4P   Central Toronto   
103         M5P   Central Toronto   
104         M6P      West Toronto   
107         M9P         Etobicoke   
108         M1R       Scarborough   
109         M2R        North York   
111         M4R   Central Toronto   
112         M5R   Central Toronto   
113         M6R      West Toronto   
114         M7R       Mississauga   
116         M9R         Etobicoke   
117         M1S       Scarborough   
120         M4S   Central Toronto   
121         M5S  Downtown Toronto   
122         M6S      West Toronto   
126         M1T       Scarborough   
129         M4T   Central Toronto   
130         M5T  Downtown Toronto   
135         M1V       Scarborough   
138         M4V   Central Toronto   
139         M5V  Downtown Toronto   
142         M8V         Etobicoke   
143         M9V         Etobicoke   
144         M1W       Scarborough   
147         M4W  Downtown Toronto   
148         M5W  Downtown Toronto   
151         M8W         Etobicoke   
152         M9W         Etobicoke   
153         M1X       Scarborough   
156         M4X  Downtown Toronto   
157         M5X  Downtown Toronto   
160         M8X         Etobicoke   
165         M4Y  Downtown Toronto   
168         M7Y      East Toronto   
169         M8Y         Etobicoke   
178         M8Z         Etobicoke   

                                         Neighbourhood  
2                                            Parkwoods  
3                                     Vic

In [103]:
df.rename(columns={'Neighbourhood': 'Neighborhood'}, inplace=True)
df = df.sort_values('Postal Code').reset_index(drop = True)
df

Postal Code           Borough  \
0           M1B       Scarborough   
1           M1C       Scarborough   
2           M1E       Scarborough   
3           M1G       Scarborough   
4           M1H       Scarborough   
5           M1J       Scarborough   
6           M1K       Scarborough   
7           M1L       Scarborough   
8           M1M       Scarborough   
9           M1N       Scarborough   
10          M1P       Scarborough   
11          M1R       Scarborough   
12          M1S       Scarborough   
13          M1T       Scarborough   
14          M1V       Scarborough   
15          M1W       Scarborough   
16          M1X       Scarborough   
17          M2H        North York   
18          M2J        North York   
19          M2K        North York   
20          M2L        North York   
21          M2M        North York   
22          M2N        North York   
23          M2P        North York   
24          M2R        North York   
25          M3A        North York   
26          M3B        North York   
27          M3C        North York   
28          M3H        North York   
29          M3J        North York   
30          M3K        North York   
31          M3L        North York   
32          M3M        North York   
33          M3N        North York   
34          M4A        North York   
35          M4B         East York   
36          M4C         East York   
37          M4E      East Toronto   
38          M4G         East York   
39          M4H         East York   
40          M4J         East York   
41          M4K      East Toronto   
42          M4L      East Toronto   
43          M4M      East Toronto   
44          M4N   Central Toronto   
45          M4P   Central Toronto   
46          M4R   Central Toronto   
47          M4S   Central Toronto   
48          M4T   Central Toronto   
49          M4V   Central Toronto   
50          M4W  Downtown Toronto   
51          M4X  Downtown Toronto   
52          M4Y  Downtown Toronto   
53          M5A  Downtown Toronto   
54          M5B  Downtown Toronto   
55          M5C  Downtown Toronto   
56          M5E  Downtown Toronto   
57          M5G  Downtown Toronto   
58          M5H  Downtown Toronto   
59          M5J  Downtown Toronto   
60          M5K  Downtown Toronto   
61          M5L  Downtown Toronto   
62          M5M        North York   
63          M5N   Central Toronto   
64          M5P   Central Toronto   
65          M5R   Central Toronto   
66          M5S  Downtown Toronto   
67          M5T  Downtown Toronto   
68          M5V  Downtown Toronto   
69          M5W  Downtown Toronto   
70          M5X  Downtown Toronto   
71          M6A        North York   
72          M6B        North York   
73          M6C              York   
74          M6E              York   
75          M6G  Downtown Toronto   
76          M6H      West Toronto   
77          M6J      West Toronto   
78          M6K      West Toronto   
79          M6L        North York   
80          M6M              York   
81          M6N              York   
82          M6P      West Toronto   
83          M6R      West Toronto   
84          M6S      West Toronto   
85          M7A  Downtown Toronto   
86          M7R       Mississauga   
87          M7Y      East Toronto   
88          M8V         Etobicoke   
89          M8W         Etobicoke   
90          M8X         Etobicoke   
91          M8Y         Etobicoke   
92          M8Z         Etobicoke   
93          M9A         Etobicoke   
94          M9B         Etobicoke   
95          M9C         Etobicoke   
96          M9L        North York   
97          M9M        North York   
98          M9N              York   
99          M9P         Etobicoke   
100         M9R         Etobicoke   
101         M9V         Etobicoke   
102         M9W         Etobicoke   

                                          Neighborhood  
0                                       Malvern, Rouge  
1               Rouge Hill, Port Union, H

In [104]:
df.loc[df['Neighborhood'] == "Not assigned", 'Neighborhood'] = df['Borough']

In [105]:
df.shape

(103, 3)

# Getting neighborhood coordinates using Geospatial Data

In [106]:
df['Latitude'] = df['Longitude'] = ""

dfc = pd.read_csv("https://cocl.us/Geospatial_data")

dfc.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [107]:
for i in range(df.shape[0]):
    postalcode = df.iloc[i, 0]
    
    for j in range(dfc.shape[0]):
        if dfc.iloc[j, 0] == postalcode:
            df.iloc[i, 3] = dfc.iloc[j, 1]
            df.iloc[i, 4] = dfc.iloc[j, 2]
            
df.head()

Postal Code      Borough                            Neighborhood Latitude  \
0         M1B  Scarborough                          Malvern, Rouge  43.8067   
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.7845   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.7636   
3         M1G  Scarborough                                  Woburn   43.771   
4         M1H  Scarborough                               Cedarbrae  43.7731   

  Longitude  
0  -79.1944  
1  -79.1605  
2  -79.1887  
3  -79.2169  
4  -79.2395

# Clustering

In [108]:
# !conda install -c conda-forge geopy --yes
!pip install geopy

In [109]:
!pip install folium

import folium # map rendering library

address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinates of Toronto are 43.6534817, -79.3839347.


#### Create a map of Toronto with neighborhoods superimposed on top.

In [110]:
# create map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, borough, neighborhood in zip(df['Latitude'], df['Longitude'], df['Borough'], df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  
    
map_toronto

#### Define Foursquare Credentials and Version

In [111]:
CLIENT_ID = 'SCYIJBZ5AL4YVV5HQKIEIPZONX5FQUIHBGBU0DIA4M3IORFI' # your Foursquare ID
CLIENT_SECRET = 'KOROAKFNWIKP31FLLQXDCIUQQ3ZVK2QKKXWK3ROF2JENHJHT' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: SCYIJBZ5AL4YVV5HQKIEIPZONX5FQUIHBGBU0DIA4M3IORFI
CLIENT_SECRET:KOROAKFNWIKP31FLLQXDCIUQQ3ZVK2QKKXWK3ROF2JENHJHT


In [112]:
df.head()

Postal Code      Borough                            Neighborhood Latitude  \
0         M1B  Scarborough                          Malvern, Rouge  43.8067   
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.7845   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.7636   
3         M1G  Scarborough                                  Woburn   43.771   
4         M1H  Scarborough                               Cedarbrae  43.7731   

  Longitude  
0  -79.1944  
1  -79.1605  
2  -79.1887  
3  -79.2169  
4  -79.2395

#### Let's explore the first neighborhood in our dataframe.

In [113]:
df.loc[0, 'Neighborhood']

'Malvern, Rouge'

In [114]:
neighborhood_latitude = df.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = df.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = df.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Malvern, Rouge are 43.806686299999996, -79.19435340000001.


#### Now, let's get the top 100 venues that are in Malvern, Rouge within a radius of 500 meters.

In [115]:
# LIMIT = 100 # limit of number of venues returned by Foursquare API
# radius = 500 # define radius
# url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
#     CLIENT_ID, 
#     CLIENT_SECRET, 
#     VERSION, 
#     neighborhood_latitude, 
#     neighborhood_longitude, 
#     radius, 
#     LIMIT)

# results = requests.get(url).json()

# # function that extracts the category of the venue
# def get_category_type(row):
#     try:
#         categories_list = row['categories']
#     except:
#         categories_list = row['venue.categories']
        
#     if len(categories_list) == 0:
#         return None
#     else:
#         return categories_list[0]['name']
    
# # clean the json and structure it into a *pandas* dataframe.
# venues = results['response']['groups'][0]['items']
    
# nearby_venues = json_normalize(venues) # flatten JSON

# # filter columns
# filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
# nearby_venues =nearby_venues.loc[:, filtered_columns]

# # filter the category for each row
# nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# # clean columns
# nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

# nearby_venues.head()

In [116]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

1 venues were returned by Foursquare.


#### Let's create a function to repeat the same process to all the neighborhoods in Toronto

In [117]:
def getNearbyVenues(names, latitudes, longitudes, radius = 500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [118]:
toronto_venues = getNearbyVenues(names = df['Neighborhood'],
                                   latitudes = df['Latitude'],
                                   longitudes = df['Longitude']
                                  )

Malvern, Rouge
Rouge Hill, Port Union, Highland Creek
Guildwood, Morningside, West Hill
Woburn
Cedarbrae
Scarborough Village
Kennedy Park, Ionview, East Birchmount Park
Golden Mile, Clairlea, Oakridge
Cliffside, Cliffcrest, Scarborough Village West
Birch Cliff, Cliffside West
Dorset Park, Wexford Heights, Scarborough Town Centre
Wexford, Maryvale
Agincourt
Clarks Corners, Tam O'Shanter, Sullivan
Milliken, Agincourt North, Steeles East, L'Amoreaux East
Steeles West, L'Amoreaux West
Upper Rouge
Hillcrest Village
Fairview, Henry Farm, Oriole
Bayview Village
York Mills, Silver Hills
Willowdale, Newtonbrook
Willowdale, Willowdale East
York Mills West
Willowdale, Willowdale West
Parkwoods
Don Mills
Don Mills
Bathurst Manor, Wilson Heights, Downsview North
Northwood Park, York University
Downsview
Downsview
Downsview
Downsview
Victoria Village
Parkview Hill, Woodbine Gardens
Woodbine Heights
The Beaches
Leaside
Thorncliffe Park
East Toronto, Broadview North (Old East York)
The Danforth West, 

In [119]:
print(toronto_venues.shape)
toronto_venues.head()

(2153, 7)


Neighborhood  Neighborhood Latitude  \
0                          Malvern, Rouge              43.806686   
1  Rouge Hill, Port Union, Highland Creek              43.784535   
2  Rouge Hill, Port Union, Highland Creek              43.784535   
3       Guildwood, Morningside, West Hill              43.763573   
4       Guildwood, Morningside, West Hill              43.763573   

   Neighborhood Longitude                        Venue  Venue Latitude  \
0              -79.194353                      Wendy’s       43.807448   
1              -79.160497  Great Shine Window Cleaning       43.783145   
2              -79.160497        Royal Canadian Legion       43.782533   
3              -79.188711               RBC Royal Bank       43.766790   
4              -79.188711            G & G Electronics       43.765309   

   Venue Longitude        Venue Category  
0       -79.199056  Fast Food Restaurant  
1       -79.157431          Home Service  
2       -79.163085                   Bar  
3       -79.191151                  Bank  
4       -79.191537     Electronics Store

Let's check how many venues were returned for each neighborhood

In [120]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               5   
Alderwood, Long Branch                                                  8   
Bathurst Manor, Wilson Heights, Downsview North                        20   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      25   
Berczy Park                                                            58   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           24   
Business reply mail Processing Centre, South Ce...                     19   
CN Tower, King and Spadina, Railway Lands, Harb...                     18   
Caledonia-Fairbanks                                                     4   
Canada Post Gateway Processing Centre                                  13   
Cedarbrae                                                               9   
Central Bay Street                                                     65   
Christie                                                               16   
Church and Wellesley                                                   78   
Clarks Corners, Tam O'Shanter, Sullivan                                11   
Cliffside, Cliffcrest, Scarborough Village West                         3   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             36   
Davisville North                                                        9   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              25   
Dorset Park, Wexford Heights, Scarborough Town ...                      6   
Downsview                                                              17   
Dufferin, Dovercourt Village                                           18   
East Toronto, Broadview North (Old East York)                           3   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      9   
Fairview, Henry Farm, Oriole                                           64   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               4   
Golden Mile, Clairlea, Oakridge                                        10   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          24   
Hillcrest Village                                                       4   
Humber Summit                                                           2   
Humberlea, Emery                                                        1   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         19   
Kennedy Park, Ionview, East Birchmount Park                             5   
Kensington Market, Chinatown, Grange Park                              66   
Kingsview Village, St. Phillips, Martin Grove G...                      4   
Lawrence Manor, Lawrence Heights                                       10   
Lawrence Park                                                           4   
Leaside                                                                35   
Little Portugal, Trinity                                               47   
Malvern, Rouge                                                          1   
Milliken, Agincourt North, Steeles East, L'Amor.

Let's take a look at some of the venues:

In [121]:
toronto_venues['Venue Category'].unique()[:50]

array(['Fast Food Restaurant', 'Home Service', 'Bar', 'Bank',
       'Electronics Store', 'Restaurant', 'Mexican Restaurant',
       'Rental Car Location', 'Medical Center', 'Intersection',
       'Breakfast Spot', 'Coffee Shop', 'Korean Restaurant',
       'Hakka Restaurant', 'Caribbean Restaurant', 'Thai Restaurant',
       'Athletics & Sports', 'Gas Station', 'Bakery', 'Lounge',
       'Fried Chicken Joint', 'Playground', 'Department Store',
       'Chinese Restaurant', 'Hobby Shop', 'Discount Store',
       'Ice Cream Shop', 'Bus Line', 'Metro Station', 'Bus Station',
       'Park', 'Soccer Field', 'Motel', 'American Restaurant',
       'Skating Rink', 'Café', 'General Entertainment', 'College Stadium',
       'Indian Restaurant', 'Pet Store', 'Vietnamese Restaurant',
       'Gaming Cafe', 'Sandwich Place', 'Middle Eastern Restaurant',
       'Shopping Mall', 'Auto Garage', 'Latin American Restaurant',
       'Clothing Store', 'Italian Restaurant', 'Noodle House'],
      dtype=obje

#### Let's find out how many unique categories can be curated from all the returned venues

In [122]:
print('There are {} unique categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 269 unique categories.


In [123]:
"Italian Restaurant" in toronto_venues['Venue Category'].unique()

True

### Analyze Each Neighborhood

In [124]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighborhoods  Accessories Store  \
0                          Malvern, Rouge                  0   
1  Rouge Hill, Port Union, Highland Creek                  0   
2  Rouge Hill, Port Union, Highland Creek                  0   
3       Guildwood, Morningside, West Hill                  0   
4       Guildwood, Morningside, West Hill                  0   

   Afghan Restaurant  Airport  Airport Food Court  Airport Gate  \
0                  0        0                   0             0   
1                  0        0                   0             0   
2                  0        0                   0             0   
3                  0        0                   0             0   
4                  0        0                   0             0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Garage  Auto Workshop  \
0                 0                   0            0              0   
1                 0                   0            0              0   
2                 0                   0            0              0   
3                 0                   0            0              0   
4                 0                   0            0              0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0          0           0           0       0     0    0               0   
1          0           0           0       0     0    0               0   
2          0           0           0       0     0    1               0   
3          0           0           0       0     1    0               0   
4          0           0           0       0     0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Beach  \
0                 0                 0                   0      0   
1                 0                 0                   0      0   
2                 0                 0                   0      0   
3                 0                 0                   0      0   
4                 0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0   

In [125]:
toronto_onehot.shape

(2153, 270)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [126]:
toronto_grouped = toronto_onehot.groupby('Neighborhoods').mean().reset_index()
toronto_grouped

Neighborhoods  Accessories Store  \
0                                           Agincourt                0.0   
1                              Alderwood, Long Branch                0.0   
2     Bathurst Manor, Wilson Heights, Downsview North                0.0   
3                                     Bayview Village                0.0   
4                   Bedford Park, Lawrence Manor East                0.0   
5                                         Berczy Park                0.0   
6                         Birch Cliff, Cliffside West                0.0   
7        Brockton, Parkdale Village, Exhibition Place                0.0   
8   Business reply mail Processing Centre, South C...                0.0   
9   CN Tower, King and Spadina, Railway Lands, Har...                0.0   
10                                Caledonia-Fairbanks                0.0   
11              Canada Post Gateway Processing Centre                0.0   
12                                          Cedarbrae                0.0   
13                                 Central Bay Street                0.0   
14                                           Christie                0.0   
15                               Church and Wellesley                0.0   
16            Clarks Corners, Tam O'Shanter, Sullivan                0.0   
17    Cliffside, Cliffcrest, Scarborough Village West                0.0   
18                     Commerce Court, Victoria Hotel                0.0   
19                                         Davisville                0.0   
20                                   Davisville North                0.0   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn                0.0   
22                                          Don Mills                0.0   
23  Dorset Park, Wexford Heights, Scarborough Town...                0.0   
24                                          Downsview                0.0   
25                       Dufferin, Dovercourt Village                0.0   
26      East Toronto, Broadview North (Old East York)                0.0   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...                0.0   
28                       Fairview, Henry Farm, Oriole                0.0   
29             First Canadian Place, Underground city                0.0   
30    Forest Hill North & West, Forest Hill Road Park                0.0   
31                           Garden District, Ryerson                0.0   
32                                          Glencairn                0.0   
33                    Golden Mile, Clairlea, Oakridge                0.0   
34                  Guildwood, Morningside, West Hill                0.0   
35  Harbourfront East, Union Station, Toronto Islands                0.0   
36                      High Park, The Junction South                0.0   
37                                  Hillcrest Village                0.0   
38                                      Humber Summit                0.0   
39                                   Humberlea, Emery                0.0   
40                                 Humewood-Cedarvale                0.0   
41                     India Bazaar, The Beaches West                0.0   
42        Kennedy Park, Ionview, East Birchmount Park                0.0   
43          Kensington Market, Chinatown, Grange Park                0.0   
44  Kingsview Village, St. Phillips, Martin Grove ...                0.0   
45                   Lawrence Manor, Lawrence Heights                0.1   
46                                      Lawrence Park                0.0   
47                                            Leaside                0.0   
48                           Little Portugal, Trinity                0.0   
49                                     Malvern, Rouge                0.0   
50  Milliken, Agincourt North, Steeles East, L'Amo...                0.0   
51  Mimico NW, The Queensway West, South of Bloor,...                0.0   
52          

In [127]:
toronto_grouped.shape

(94, 270)

Let's see how many neighborhoods have Italian restaurants:

In [128]:
len(toronto_grouped[toronto_grouped["Italian Restaurant"] > 0])

25

In [129]:
toronto_italian = toronto_grouped[["Neighborhoods","Italian Restaurant"]]
toronto_italian.head(5)

Neighborhoods  Italian Restaurant
0                                        Agincourt                0.00
1                           Alderwood, Long Branch                0.00
2  Bathurst Manor, Wilson Heights, Downsview North                0.00
3                                  Bayview Village                0.00
4                Bedford Park, Lawrence Manor East                0.08

## Cluster Neighborhoods

In [184]:
# set number of clusters
kclusters = 4

toronto_italian_clustering = toronto_italian.drop('Neighborhoods', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_italian_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20] 

array([0, 0, 0, 0, 3, 2, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 3, 0, 2, 1],
      dtype=int32)

In [185]:
toronto_merged = toronto_italian.copy()

# add clustering labels
toronto_merged["Cluster Labels"] = kmeans.labels_

toronto_merged.head()

Neighborhoods  Italian Restaurant  \
0                                        Agincourt                0.00   
1                           Alderwood, Long Branch                0.00   
2  Bathurst Manor, Wilson Heights, Downsview North                0.00   
3                                  Bayview Village                0.00   
4                Bedford Park, Lawrence Manor East                0.08   

   Cluster Labels  
0               0  
1               0  
2               0  
3               0  
4               3

In [186]:
toronto_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
print(toronto_merged.shape)
toronto_merged.head(5)

(94, 3)


Neighborhood  Italian Restaurant  \
0                                        Agincourt                0.00   
1                           Alderwood, Long Branch                0.00   
2  Bathurst Manor, Wilson Heights, Downsview North                0.00   
3                                  Bayview Village                0.00   
4                Bedford Park, Lawrence Manor East                0.08   

   Cluster Labels  
0               0  
1               0  
2               0  
3               0  
4               3

In [187]:
toronto_merged = toronto_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(toronto_merged.shape)
toronto_merged.head()

(2153, 9)


Neighborhood  Italian Restaurant  Cluster Labels  Neighborhood Latitude  \
0    Agincourt                 0.0               0                43.7942   
0    Agincourt                 0.0               0                43.7942   
0    Agincourt                 0.0               0                43.7942   
0    Agincourt                 0.0               0                43.7942   
0    Agincourt                 0.0               0                43.7942   

   Neighborhood Longitude                        Venue  Venue Latitude  \
0              -79.262029  Panagio's Breakfast & Lunch       43.792370   
0              -79.262029                     Twilight       43.791999   
0              -79.262029                El Pulgarcito       43.792648   
0              -79.262029                       Mark's       43.791179   
0              -79.262029              Commander Arena       43.794867   

   Venue Longitude             Venue Category  
0       -79.260203             Breakfast Spot  
0       -79.258584                     Lounge  
0       -79.259208  Latin American Restaurant  
0       -79.259714             Clothing Store  
0       -79.267989               Skating Rink

In [188]:
toronto_merged.sort_values(["Cluster Labels"], inplace=True)
toronto_merged.head(10)

Neighborhood  Italian Restaurant  Cluster Labels  \
0                          Agincourt                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   
45  Lawrence Manor, Lawrence Heights                 0.0               0   

    Neighborhood Latitude  Neighborhood Longitude  \
0               43.794200              -79.262029   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   
45              43.718518              -79.464763   

                                    Venue  Venue Latitude  Venue Longitude  \
0             Panagio's Breakfast & Lunch       43.792370       -79.260203   
45                             Party City       43.719418       -79.459317   
45                International Clothiers       43.717997       -79.466720   
45         Rinx Real Entertainment Centre       43.717842       -79.462231   
45                    Ardene Shoes Outlet       43.718892       -79.461344   
45            Orfus Road Shopping Outlets       43.719045       -79.460849   
45                            Tim Hortons       43.719427       -79.467995   
45         Lac Vien Vietnamese Restaurant       43.721259       -79.468472   
45                     Canadian Appliance       43.722110       -79.467266   
45  Kitchen Stuff Plus (Clearance Outlet)       43.719096       -79.462675   

            Venue Category  
0           Breakfast Spot  
45      Miscellaneous Shop  
45          Clothing Store  
45             Event Space  
45       Accessories Store  
45          Clothing Store  
45             Coffee Shop  
45   Vietnamese Restaurant  
45  Furniture / Home Store  
45  Furniture / Home Store

### Let's visualize the clusters:

In [189]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighborhood Latitude'], toronto_merged['Neighborhood Longitude'], toronto_merged['Neighborhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color = rainbow[cluster-1],
        fill = True,
        fill_color = rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

#### Cluster 0

In [190]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 0)  & (toronto_merged['Venue Category'] == 'Italian Restaurant')]

Neighborhood  Italian Restaurant  \
29  First Canadian Place, Underground city                0.01   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude     Venue  \
29               0              43.648429               -79.38228  Mercatto   

    Venue Latitude  Venue Longitude      Venue Category  
29       43.650243        -79.38082  Italian Restaurant

#### Cluster 1

In [191]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 1)  & (toronto_merged['Venue Category'] == 'Italian Restaurant')]

Neighborhood  Italian Restaurant  \
68                            Runnymede, Swansea            0.057143   
68                            Runnymede, Swansea            0.057143   
13                            Central Bay Street            0.061538   
13                            Central Bay Street            0.061538   
14                                      Christie            0.062500   
13                            Central Bay Street            0.061538   
13                            Central Bay Street            0.061538   
75                                Stn A PO Boxes            0.040816   
75                                Stn A PO Boxes            0.040816   
7   Brockton, Parkdale Village, Exhibition Place            0.041667   
75                                Stn A PO Boxes            0.040816   
75                                Stn A PO Boxes            0.040816   
73                   St. James Town, Cabbagetown            0.047619   
73                   St. James Town, Cabbagetown            0.047619   
36                 High Park, The Junction South            0.041667   
19                                    Davisville            0.055556   
19                                    Davisville            0.055556   
41                India Bazaar, The Beaches West            0.052632   
22                                     Don Mills            0.040000   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
68               1              43.651571              -79.484450   
68               1              43.651571              -79.484450   
13               1              43.657952              -79.387383   
13               1              43.657952              -79.387383   
14               1              43.669542              -79.422564   
13               1              43.657952              -79.387383   
13               1              43.657952              -79.387383   
75               1              43.646435              -79.374846   
75               1              43.646435              -79.374846   
7                1              43.636847              -79.428191   
75               1              43.646435              -79.374846   
75               1              43.646435              -79.374846   
73               1              43.667967              -79.367675   
73               1              43.667967              -79.367675   
36               1              43.661608              -79.464763   
19               1              43.704324              -79.388790   
19               1              43.704324              -79.388790   
41               1              43.668999              -79.315572   
22               1              43.725900              -79.340923   

                               Venue  Venue Latitude  Venue Longitude  \
68        Goodfellas Wood Oven Pizza       43.648224       -79.486356   
68                             Campo       43.655191       -79.487067   
13                     Sambuca Grill       43.656110       -79.392946   
13                             Tosto       43.661198       -79.386414   
14                    Vinny’s Panini       43.670679       -79.426148   
13  Scaddabush Italian Kitchen & Bar       43.658920       -79.382891   
13                          Mercatto       43.660391       -79.387664   
75         The Old Spaghetti Factory       43.646964       -79.374403   
75                           Carisma       43.649617       -79.375434   
7                            Caffino       43.639021       -79.425289   
75                             Mirto       43.650702       -79.376307   
75            Metropolitan Resto Bar       43.650062       -79.377181   
73                          Hey Lucy       43.664075       -79.368655   
73                          F'Amelia       43.667536       -79.368613   
36                              nodo       43.665303       -79.465621   
19              Florentia Ristorante       43.

#### Cluster 2

In [192]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 2)  & (toronto_merged['Venue Category'] == 'Italian Restaurant')]

Neighborhood  Italian Restaurant  \
35  Harbourfront East, Union Station, Toronto Islands            0.020000   
84                     University of Toronto, Harbord            0.028571   
76                                    Studio District            0.025000   
35  Harbourfront East, Union Station, Toronto Islands            0.020000   
83           Toronto Dominion Centre, Design Exchange            0.020000   
83           Toronto Dominion Centre, Design Exchange            0.020000   
5                                         Berczy Park            0.017241   
48                           Little Portugal, Trinity            0.021277   
31                           Garden District, Ryerson            0.030000   
31                           Garden District, Ryerson            0.030000   
31                           Garden District, Ryerson            0.030000   
62        Queen's Park, Ontario Provincial Government            0.030303   
72                                     St. James Town            0.023256   
18                     Commerce Court, Victoria Hotel            0.030000   
72                                     St. James Town            0.023256   
18                     Commerce Court, Victoria Hotel            0.030000   
18                     Commerce Court, Victoria Hotel            0.030000   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
35               2              43.640816              -79.381752   
84               2              43.662696              -79.400049   
76               2              43.659526              -79.340923   
35               2              43.640816              -79.381752   
83               2              43.647177              -79.381576   
83               2              43.647177              -79.381576   
5                2              43.644771              -79.373306   
48               2              43.647927              -79.419750   
31               2              43.657162              -79.378937   
31               2              43.657162              -79.378937   
31               2              43.657162              -79.378937   
62               2              43.662301              -79.389494   
72               2              43.651494              -79.375418   
18               2              43.648198              -79.379817   
72               2              43.651494              -79.375418   
18               2              43.648198              -79.379817   
18               2              43.648198              -79.379817   

                               Venue  Venue Latitude  Venue Longitude  \
35                  Taverna Mercatto       43.642625       -79.383257   
84                       Piano Piano       43.662949       -79.402898   
76                           Baldini       43.661300       -79.339027   
35                       Amano Pasta       43.644919       -79.382358   
83                              TOCA       43.645431       -79.387059   
83                          Mercatto       43.650243       -79.380820   
5          The Old Spaghetti Factory       43.646964       -79.374403   
48                           Ufficio       43.649439       -79.423014   
31  Scaddabush Italian Kitchen & Bar       43.658920       -79.382891   
31              Donatello Restaurant       43.657489       -79.383605   
31                Trattoria Mercatto       43.654453       -79.380974   
62                          Mercatto       43.660391       -79.387664   
72                           Terroni       43.650927       -79.375602   
18                          Mercatto       43.650243       -79.380820   
72                          Mercatto       43.650243       -79.380820   
18                           Carisma       43.649617       -79.375434   
18                           Terroni       43.650927       -79.375602   

        Venue Category  
35  Italian Restaurant  
84  Italian Restaurant  
76  Italian Restauran

#### Cluster 3

In [193]:
toronto_merged.loc[(toronto_merged['Cluster Labels'] == 3)  & (toronto_merged['Venue Category'] == 'Italian Restaurant')]

Neighborhood  Italian Restaurant  \
80             The Danforth West, Riverdale            0.071429   
4         Bedford Park, Lawrence Manor East            0.080000   
80             The Danforth West, Riverdale            0.071429   
80             The Danforth West, Riverdale            0.071429   
16  Clarks Corners, Tam O'Shanter, Sullivan            0.090909   
59                   Parkdale, Roncesvalles            0.071429   
4         Bedford Park, Lawrence Manor East            0.080000   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
80               3              43.679557              -79.352188   
4                3              43.733283              -79.419750   
80               3              43.679557              -79.352188   
80               3              43.679557              -79.352188   
16               3              43.781638              -79.304302   
59               3              43.648960              -79.456325   
4                3              43.733283              -79.419750   

                           Venue  Venue Latitude  Venue Longitude  \
80               Cafe Fiorentina       43.677743       -79.350115   
4                    Francobollo       43.734557       -79.419549   
80                     7 Numbers       43.677062       -79.353934   
80       IL FORNELLO on Danforth       43.678604       -79.346904   
16        Remezzo Italian Bistro       43.778649       -79.308264   
59  Domani Restaurant & Wine Bar       43.649235       -79.450229   
4                     Il Fornaro       43.734073       -79.419870   

        Venue Category  
80  Italian Restaurant  
4   Italian Restaurant  
80  Italian Restaurant  
80  Italian Restaurant  
16  Italian Restaurant  
59  Italian Restaurant  
4   Italian Restaurant